## Overview

This notebook will show you how to create and query a table or DataFrame that you uploaded to DBFS. [DBFS](https://docs.databricks.com/user-guide/dbfs-databricks-file-system.html) is a Databricks File System that allows you to store data for querying inside of Databricks. This notebook assumes that you have a file already inside of DBFS that you would like to read from.

This notebook is written in **Python** so the default cell type is Python. However, you can use different languages by using the `%LANGUAGE` syntax. Python, Scala, SQL, and R are all supported.

###0) Setup

In [0]:
# INSTALL PACKAGES
dbutils.library.installPyPI("pandas")
dbutils.library.restartPython()

In [0]:
# IMPORT PACKAGES
import pandas as pd
import numpy as np
import re
from functools import reduce
from pyspark.sql import DataFrame
from pyspark.sql.types import StringType, IntegerType
import pyspark.sql.functions as F

###1) Load files

In [0]:
# LOAD FILES
# Values
df_values = spark.read.format('csv')\
                      .option('inferSchema', 'true')\
                      .option('header', 'true')\
                      .load('/FileStore/tables/train_values.csv')
df_values.createOrReplaceTempView('df_values')

df_labels = spark.read.format('csv')\
                      .option('inferSchema', 'true')\
                      .option('header', 'true')\
                      .load('/FileStore/tables/train_labels.csv')
df_labels.createOrReplaceTempView('df_labels')

# Join tables together
df_all = df_values.join(df_labels, ['row_id'])
df_all.createOrReplaceTempView('df_all')
df = df_all.toPandas()

In [0]:
display(df_labels)

row_id income 0 46.9 1 26.7 3 28.1 4 41.6 5 34.3 6 23.2 7 59.7 14 32.9 15 25.7 16 19.3 17 18.7 18 26.5 19 23.2 22 26.5 23 26.6 25 21.8 26 22.7 27 30.4 28 33.3 29 39.4 31 36.4 32 40.2 33 17.4 35 29.8 36 25.0 37 22.9 38 31.7 40 18.1 41 17.5 46 18.6 48 43.2 50 23.6 53 28.1 55 19.4 56 17.9 57 42.4 59 45.4 60 29.5 66 45.1 67 27.0 69 20.1 72 35.1 73 88.3 74 20.1 75 28.8 76 50.5 77 34.4 78 25.8 79 33.8 80 39.8 81 19.9 82 38.9 84 49.8 85 35.6 86 31.6 88 21.3 89 64.7 90 62.4 92 43.4 94 68.4 95 34.9 96 19.1 97 36.9 98 26.5 99 21.5 101 19.5 103 14.3 109 27.4 110 34.5 112 27.0 115 38.6 117 24.3 119 16.5 120 28.7 123 33.1 124 19.8 126 21.0 127 15.5 128 41.7 129 29.3 130 16.3 131 38.9 132 36.5 133 57.1 135 63.1 136 32.8 138 23.5 140 26.5 141 24.8 142 25.8 143 25.0 144 26.2 145 33.9 146 19.3 147 19.1 150 29.5 152 38.3 153 18.0 154 25.9 155 29.7 158 21.4 159 20.2 161 50.2 162 42.9 164 34.2 165 40.1 166 27.6 169 35.3 170 46.6 171 26.1 172 19.6 173 33.9 176 38.8 177 24.9 178 26.2 179 32.7 181 23.0 182 34.6 183 29.3 185 18.9 186 30.3 187 27.2 188 28.1 191 36.7 192 29.5 193 99.2 195 30.3 197 27.3 198 34.6 199 25.6 200 19.7 202 21.5 203 46.0 204 19.1 205 35.2 207 24.5 209 18.5 210 18.9 211 43.0 212 20.6 213 22.7 216 19.7 217 19.7 218 24.9 219 43.7 220 32.0 223 30.2 224 14.8 225 23.7 226 28.8 227 29.3 228 44.2 229 20.9 230 35.0 231 27.8 233 24.4 234 36.5 235 15.7 236 19.2 237 21.3 238 44.8 242 16.7 243 17.1 244 70.1 245 26.9 246 44.0 250 34.2 253 26.5 255 30.2 256 43.5 257 41.3 258 36.1 259 32.2 264 28.0 265 24.8 266 18.8 268 21.8 269 43.8 270 49.9 273 39.0 279 25.9 280 36.6 282 29.1 284 18.2 285 38.3 287 23.2 288 27.3 289 18.4 291 24.3 292 17.0 294 21.5 295 41.4 296 20.0 297 32.1 299 24.5 300 38.8 301 44.9 302 25.6 303 15.8 304 34.4 305 41.8 307 63.3 308 39.9 309 39.8 312 70.7 313 30.4 314 15.6 315 26.5 317 25.3 318 14.9 319 31.2 322 36.6 323 44.2 326 35.6 328 33.9 329 21.7 330 26.7 331 33.6 332 22.3 333 25.9 335 19.5 336 27.6 337 22.7 338 19.6 339 36.4 343 35.8 344 24.8 346 23.6 350 31.8 352 23.8 353 23.3 354 27.5 356 41.9 357 20.0 358 32.1 359 18.1 360 37.3 361 35.3 362 22.2 363 50.8 364 22.8 365 37.7 367 23.1 371 19.8 372 32.0 374 33.4 377 26.9 378 33.4 380 17.1 381 16.5 382 41.8 383 26.7 385 33.2 386 26.2 387 78.3 389 31.2 391 20.0 392 59.1 393 42.5 395 23.4 396 27.4 397 18.1 398 33.9 399 18.7 400 27.5 401 20.2 402 30.5 403 36.2 404 27.4 405 24.3 408 23.8 409 18.2 410 15.3 411 48.2 413 17.1 415 20.2 417 25.4 419 42.5 420 31.9 421 31.5 422 61.0 423 33.3 427 34.9 428 32.4 429 25.8 430 51.3 431 13.7 433 46.0 436 18.1 438 19.4 439 50.2 440 48.7 441 38.5 442 22.2 443 17.6 444 46.2 445 42.2 448 51.3 449 26.6 450 35.4 451 17.3 452 28.2 453 36.0 455 25.4 456 24.4 457 29.1 458 42.1 460 28.6 461 26.9 462 35.4 467 30.4 468 20.3 469 23.1 473 22.5 474 32.6 475 21.9 476 35.3 477 31.7 478 37.9 480 41.8 481 56.7 482 22.1 484 14.6 485 40.9 486 57.0 487 22.5 490 56.0 491 27.8 492 21.0 493 19.3 494 32.0 495 19.3 496 19.7 497 16.4 500 19.3 503 23.7 505 27.2 508 28.9 509 34.0 511 27.1 515 30.9 516 29.5 517 26.9 520 28.0 521 17.2 522 21.9 523 26.7 524 32.3 525 31.8 526 17.3 528 37.5 531 43.5 532 26.3 533 19.8 535 23.3 537 24.9 538 32.9 540 19.6 541 40.4 543 14.9 545 36.7 546 26.8 547 32.0 550 31.7 551 33.0 552 19.0 554 20.9 556 24.1 557 29.4 559 41.7 560 38.3 561 27.6 562 39.0 563 29.9 564 28.1 565 28.6 568 17.0 569 29.2 571 40.9 572 39.9 573 23.3 575 22.2 577 22.0 580 32.3 581 40.3 583 20.8 584 24.8 587 39.0 588 10.6 589 29.8 590 24.8 591 34.4 595 16.7 596 37.9 597 21.4 598 50.6 599 47.0 600 23.0 601 26.2 602 22.4 603 28.1 604 41.8 605 19.0 607 19.3 610 35.6 615 16.4 616 25.3 618 18.6 619 27.4 620 25.6 623 35.0 628 35.9 629 27.7 631 25.7 632 35.6 633 38.5 635 26.9 636 35.8 638 22.8 643 23.9 645 26.4 646 76.5 647 18.1 648 20.1 651 26.4 652 43.2 655 23.6 657 35.7 658 25.4 661 60.2 662 17.6 663 29.5 665 27.0 666 36.1 668 17.1 669 17.0 671 33.8 674 39.8 676 28.5 677 19.2 679 28.9 680 29.4 682 25.8 687 24.8 689 20.8 691 17.1 692 26.2 693 28.2 695 32.7 696 20.0 697 17.4

In [0]:
# GET COLUMN INFO
df_values.dtypes

Out[4]: [('row_id', 'int'),
 ('academics__program_assoc_agriculture', 'double'),
 ('academics__program_assoc_architecture', 'double'),
 ('academics__program_assoc_biological', 'double'),
 ('academics__program_assoc_business_marketing', 'double'),
 ('academics__program_assoc_communication', 'double'),
 ('academics__program_assoc_communications_technology', 'double'),
 ('academics__program_assoc_computer', 'double'),
 ('academics__program_assoc_construction', 'double'),
 ('academics__program_assoc_education', 'double'),
 ('academics__program_assoc_engineering', 'double'),
 ('academics__program_assoc_engineering_technology', 'double'),
 ('academics__program_assoc_english', 'double'),
 ('academics__program_assoc_ethnic_cultural_gender', 'double'),
 ('academics__program_assoc_family_consumer_science', 'double'),
 ('academics__program_assoc_health', 'double'),
 ('academics__program_assoc_history', 'double'),
 ('academics__program_assoc_humanities', 'double'),
 ('academics__program_assoc_language', 'double'),
 ('academics__program_assoc_legal', 'double'),
 ('academics__program_assoc_library', 'double'),
 ('academics__program_assoc_mathematics', 'double'),
 ('academics__program_assoc_mechanic_repair_technology', 'double'),
 ('academics__program_assoc_military', 'double'),
 ('academics__program_assoc_multidiscipline', 'double'),
 ('academics__program_assoc_parks_recreation_fitness', 'double'),
 ('academics__program_assoc_personal_culinary', 'double'),
 ('academics__program_assoc_philosophy_religious', 'double'),
 ('academics__program_assoc_physical_science', 'double'),
 ('academics__program_assoc_precision_production', 'double'),
 ('academics__program_assoc_psychology', 'double'),
 ('academics__program_assoc_public_administration_social_service', 'double'),
 ('academics__program_assoc_resources', 'double'),
 ('academics__program_assoc_science_technology', 'double'),
 ('academics__program_assoc_security_law_enforcement', 'double'),
 ('academics__program_assoc_social_science', 'double'),
 ('academics__program_assoc_theology_religious_vocation', 'double'),
 ('academics__program_assoc_transportation', 'double'),
 ('academics__program_assoc_visual_performing', 'double'),
 ('academics__program_bachelors_agriculture', 'double'),
 ('academics__program_bachelors_architecture', 'double'),
 ('academics__program_bachelors_biological', 'double'),
 ('academics__program_bachelors_business_marketing', 'double'),
 ('academics__program_bachelors_communication', 'double'),
 ('academics__program_bachelors_communications_technology', 'double'),
 ('academics__program_bachelors_computer', 'double'),
 ('academics__program_bachelors_construction', 'double'),
 ('academics__program_bachelors_education', 'double'),
 ('academics__program_bachelors_engineering', 'double'),
 ('academics__program_bachelors_engineering_technology', 'double'),
 ('academics__program_bachelors_english', 'double'),
 ('academics__program_bachelors_ethnic_cultural_gender', 'double'),
 ('academics__program_bachelors_family_consumer_science', 'double'),
 ('academics__program_bachelors_health', 'double'),
 ('academics__program_bachelors_history', 'double'),
 ('academics__program_bachelors_humanities', 'double'),
 ('academics__program_bachelors_language', 'double'),
 ('academics__program_bachelors_legal', 'double'),
 ('academics__program_bachelors_library', 'double'),
 ('academics__program_bachelors_mathematics', 'double'),
 ('academics__program_bachelors_mechanic_repair_technology', 'double'),
 ('academics__program_bachelors_military', 'double'),
 ('academics__program_bachelors_multidiscipline', 'double'),
 ('academics__program_bachelors_parks_recreation_fitness', 'double'),
 ('academics__program_bachelors_personal_culinary', 'double'),
 ('academics__program_bachelors_philosophy_religious', 'double'),
 ('academics__program_bachelors_physical_science', 'double'),
 ('academics__program_bachelors_precision_production', 'double'),
 ('academics__program_bachelors_psychology', 'double'),
 ('academic

###2) Preprocessing

In [0]:
# GROUP COLUMNS
def getcolnames(substring):
  return [col for col in df_all.columns if substring in col]

_col_groups = ['academics__program_assoc', 'academics__program_bachelors',
               'academics__program_certificate', 'academics__program_certificate_lt_1', 'academics__program_certificate_lt_2', 'academics__program_certificate_lt_4', 'academics__program_percentage',
               'admissions__act_scores', 'admissions__admission_rate', 'admissions__sat_scores',
               'completion__completion_cohort', 'completion__completion_rate', 'completion__transfer_rate',
               'school__degrees', 'school__revenue', 'school__type', 'school__investment', 'school__other', 'student__demographics', 'student__retention_rate', 'student__share'
              ]
for group in _col_groups:
  if group == 'school__revenue':
    globals()[group] = ['cost__tuition_in_state', 'cost__tuition_out_of_state', 'cost__tuition_program_year', 'school__tuition_revenue_per_fte']
  elif group == 'school__type':
    globals()[group] = ['school__main_campus', 'school__online_only', 'school__ownership', 'school__region_id', 'school__state']
  elif group == 'school__investment':
    globals()[group] = ['school__faculty_salary', 'school__instructional_expenditure_per_fte']
  elif group == 'school__other':
    globals()[group] = ['school__ft_faculty_rate', 'school__institutional_characteristics_level', 'student__size']
  elif group == 'student__share':
    globals()[group] = getcolnames(group) + ['student__part_time_share']
  else:
    globals()[group] = getcolnames(group)
    
# Columns not grouped
[i for i in df_all.columns if i not in sum([globals()[x] for x in _col_groups], [])]

Out[5]: ['row_id', 'report_year', 'income']

####2.1) Academics

In [0]:
# Get distinct disciplines
degrees = [i for i in df_all.columns if i in sum([globals()[x] for x in ['academics__program_assoc', 'academics__program_bachelors', 'academics__program_certificate']], [])]
disciplines = []

for i in degrees:
  if re.search(r'certificate', i):
    disciplines.append(re.sub(r'academics__program_certificate_lt_[0-9]_yr_', '', i))
  else:
    disciplines.append(re.sub(r'academics__program_[a-z]*_', '', i))

# Assign to group
dict_discipline = {'Arts'   : ['communication', 'english', 'ethnic_cultural_gender', 'family_consumer_science', 'history', 'humanities', 'language', 'library', 'philosophy_religious', 'theology_religious_vocation', 'visual_performing'],\
                   'Bus_Edu': ['business_marketing', 'education', 'legal', 'public_administration_social_service', 'social_science'],\
                   'STEM'   : ['agriculture', 'architecture', 'biological', 'communications_technology', 'computer', 'engineering', 'mathematics', 'military', 'multidiscipline', 'physical_science', 'resources', 'science_technology'],\
                   'Health' : ['health', 'psychology'],\
                   'Other'  : ['construction', 'engineering_technology', 'mechanic_repair_technology', 'parks_recreation_fitness', 'personal_culinary', 'precision_production', 'security_law_enforcement', 'transportation']
                  }

sorted(list(set(disciplines)))

Out[6]: ['agriculture',
 'architecture',
 'biological',
 'business_marketing',
 'communication',
 'communications_technology',
 'computer',
 'construction',
 'education',
 'engineering',
 'engineering_technology',
 'english',
 'ethnic_cultural_gender',
 'family_consumer_science',
 'health',
 'history',
 'humanities',
 'language',
 'legal',
 'library',
 'mathematics',
 'mechanic_repair_technology',
 'military',
 'multidiscipline',
 'parks_recreation_fitness',
 'personal_culinary',
 'philosophy_religious',
 'physical_science',
 'precision_production',
 'psychology',
 'public_administration_social_service',
 'resources',
 'science_technology',
 'security_law_enforcement',
 'social_science',
 'theology_religious_vocation',
 'transportation',
 'visual_performing']

In [0]:
for i in dict_discipline.keys():
  print(dict_discipline[i])

['communication', 'english', 'ethnic_cultural_gender', 'family_consumer_science', 'history', 'humanities', 'language', 'library', 'philosophy_religious', 'theology_religious_vocation', 'visual_performing']
['business_marketing', 'education', 'legal', 'public_administration_social_service', 'social_science']
['agriculture', 'architecture', 'biological', 'communications_technology', 'computer', 'engineering', 'mathematics', 'military', 'multidiscipline', 'physical_science', 'resources', 'science_technology']
['health', 'psychology']
['construction', 'engineering_technology', 'mechanic_repair_technology', 'parks_recreation_fitness', 'personal_culinary', 'precision_production', 'security_law_enforcement', 'transportation']

In [0]:
#for colname in degrees:
#   df_all = df_all.withColumn(colname, F.concat(F.lit(colname+'_'), F.col(colname)))
#display(df_all.select(*[F.mean(c).alias(c) for c in degrees]))

In [0]:
# Check % of missing values
display(df_all.select([(F.count(F.when(F.col(c).isNull(), c))/F.count(F.col('Income'))).alias(c) for c in df_all.columns]))

# Drop unnecessary ones
_dropcols = sum([admissions__act_scores, admissions__admission_rate, admissions__sat_scores, completion__completion_cohort, completion__completion_rate, completion__transfer_rate],[])\
            + ['cost__tuition_program_year', 
               'student__retention_rate_four_year_full_time', 'student__retention_rate_four_year_part_time',  'student__retention_rate_lt_four_year_full_time', 'student__retention_rate_lt_four_year_part_time', 
               'student__share_firstgeneration_parents_middleschool']

# Drop columns with approx 50% or more NULLs
# Drop rows where ACADEMICS data is missing
df_drop = df_all.drop(*_dropcols)\
                .withColumn('CountNULL', sum([F.when(F.col(c).isNull(), 1).otherwise(0).alias(c) for c in degrees]))\
                .filter(F.col('CountNULL') < len(degrees))\
                .drop('CountNULL')

row_id academics__program_assoc_agriculture academics__program_assoc_architecture academics__program_assoc_biological academics__program_assoc_business_marketing academics__program_assoc_communication academics__program_assoc_communications_technology academics__program_assoc_computer academics__program_assoc_construction academics__program_assoc_education academics__program_assoc_engineering academics__program_assoc_engineering_technology academics__program_assoc_english academics__program_assoc_ethnic_cultural_gender academics__program_assoc_family_consumer_science academics__program_assoc_health academics__program_assoc_history academics__program_assoc_humanities academics__program_assoc_language academics__program_assoc_legal academics__program_assoc_library academics__program_assoc_mathematics academics__program_assoc_mechanic_repair_technology academics__program_assoc_military academics__program_assoc_multidiscipline academics__program_assoc_parks_recreation_fitness academics__program_assoc_personal_culinary academics__program_assoc_philosophy_religious academics__program_assoc_physical_science academics__program_assoc_precision_production academics__program_assoc_psychology academics__program_assoc_public_administration_social_service academics__program_assoc_resources academics__program_assoc_science_technology academics__program_assoc_security_law_enforcement academics__program_assoc_social_science academics__program_assoc_theology_religious_vocation academics__program_assoc_transportation academics__program_assoc_visual_performing academics__program_bachelors_agriculture academics__program_bachelors_architecture academics__program_bachelors_biological academics__program_bachelors_business_marketing academics__program_bachelors_communication academics__program_bachelors_communications_technology academics__program_bachelors_computer academics__program_bachelors_construction academics__program_bachelors_education academics__program_bachelors_engineering academics__program_bachelors_engineering_technology academics__program_bachelors_english academics__program_bachelors_ethnic_cultural_gender academics__program_bachelors_family_consumer_science academics__program_bachelors_health academics__program_bachelors_history academics__program_bachelors_humanities academics__program_bachelors_language academics__program_bachelors_legal academics__program_bachelors_library academics__program_bachelors_mathematics academics__program_bachelors_mechanic_repair_technology academics__program_bachelors_military academics__program_bachelors_multidiscipline academics__program_bachelors_parks_recreation_fitness academics__program_bachelors_personal_culinary academics__program_bachelors_philosophy_religious academics__program_bachelors_physical_science academics__program_bachelors_precision_production academics__program_bachelors_psychology academics__program_bachelors_public_administration_social_service academics__program_bachelors_resources academics__program_bachelors_science_technology academics__program_bachelors_security_law_enforcement academics__program_bachelors_social_science academics__program_bachelors_theology_religious_vocation academics__program_bachelors_transportation academics__program_bachelors_visual_performing academics__program_certificate_lt_1_yr_agriculture academics__program_certificate_lt_1_yr_architecture academics__program_certificate_lt_1_yr_biological academics__program_certificate_lt_1_yr_business_marketing academics__program_certificate_lt_1_yr_communication academics__program_certificate_lt_1_yr_communications_technology academics__program_certificate_lt_1_yr_computer academics__program_certificate_lt_1_yr_construction academics__program_certificate_lt_1_yr_education academics__program_certificate_lt_1_yr_engineering academics__program_certificate_lt_1_yr_engineering_technology academics__program_certificate_lt_1_yr_english academics__program_certificate_lt_1_yr_ethnic_cultural_gender academics__program_ce

In [0]:
display(df_drop.select(F.col('academics__program_assoc_agriculture').alias('Value'), 'Income')\
               .withColumn('Variable', F.lit('academics__program_assoc_agriculture'))\
               .groupBy(F.col('Variable'), F.col('Value'))\
               .agg( F.min('Income').alias('Min')\
                    ,F.expr('percentile_approx(Income, 0.25)').alias('25th')\
                    ,F.expr('percentile_approx(Income, 0.50)').alias('Median')\
                    ,F.expr('percentile_approx(Income, 0.75)').alias('75th')\
                    ,F.max('Income').alias('Max')\
                    ,F.avg('Income').alias('Mean')\
                    ,F.stddev('Income').alias('Std')
                   ))

Variable Value Min 25th Median 75th Max Mean Std academics__program_assoc_agriculture 0.0 9.4 22.6 28.6 35.7 151.5 30.57514154048715 11.593045894465279 academics__program_assoc_agriculture 2.0 24.5 26.4 28.9 32.3 44.6 31.04444444444444 6.167297265055054 academics__program_assoc_agriculture 1.0 15.1 26.0 28.5 31.3 53.1 29.13518987341772 5.099556368347291

In [0]:
# UDF: Create column with Discipline name
def f_field(col):
  # Regex field
  if re.search(r'certificate', col):
    return re.sub(r'academics__program_certificate_lt_[0-9]_yr_', '', col)
  else:
    return re.sub(r'academics__program_[a-z]*_', '', col)

udf_field = udf(lambda x: f_field(x), StringType())

# UDF: Create column with Discipline name
def f_discipline(col):
  return [i for i in dict_discipline.keys() if f_field(col) in dict_discipline[i]][0]

udf_discipline = udf(lambda x: f_discipline(x), StringType())

#UDF: Create column with Degree type:
def f_degree(col):
  # Remove first part
  _degree = re.sub(r'academics__program_', '', col)
  # Remove last part for cetificater
  if re.search(r'certificate', col):
    return re.sub(r'_lt_[0-9]_yr_[a-z_]*', '', _degree)
  else:
    return re.sub(r'_[a-z_]*', '', _degree)
  
udf_degree = udf(lambda x: f_degree(x), StringType())

# Union then calculate
_dfs = []
for colname in degrees:
  _df = df_drop.select(F.col(colname).alias('Value'), 'Income')\
               .withColumn('Variable'  , F.lit(colname))\
               .withColumn('Field'     , udf_field(F.lit(colname)))\
               .withColumn('Discipline', udf_discipline(F.lit(colname)))\
               .withColumn('Degree'    , udf_degree(F.lit(colname)))\
               .na.fill(0,['Value'])
  _dfs.append(_df)

df_union = reduce(DataFrame.unionByName, _dfs)

In [0]:
display(df_union.limit(5))

Value Income Variable Field Discipline Degree 0.0 46.9 academics__program_assoc_agriculture agriculture STEM assoc 0.0 26.7 academics__program_assoc_agriculture agriculture STEM assoc 0.0 28.1 academics__program_assoc_agriculture agriculture STEM assoc 0.0 41.6 academics__program_assoc_agriculture agriculture STEM assoc 0.0 34.3 academics__program_assoc_agriculture agriculture STEM assoc

In [0]:
# GROUP BY FULL
# 0 = Program not offered
# 1 = Program offered
# 2 = Program offered through an exclusively distance-education program
summary = df_union.groupBy(F.col('Variable'), F.col('Value'))\
                  .agg( F.min('Income').alias('Min')\
                       ,F.expr('percentile_approx(Income, 0.25)').alias('25th')\
                       ,F.expr('percentile_approx(Income, 0.50)').alias('Median')\
                       ,F.expr('percentile_approx(Income, 0.75)').alias('75th')\
                       ,F.max('Income').alias('Max')\
                       ,F.avg('Income').alias('Mean')\
                       ,F.stddev('Income').alias('Std')\
                      )\
                  .orderBy(['Value', 'Variable'])
display(summary)

Variable Value Min 25th Median 75th Max Mean Std academics__program_assoc_agriculture null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_architecture null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_biological null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_business_marketing null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_communication null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_communications_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_computer null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_construction null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_education null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_engineering null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_engineering_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_english null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_ethnic_cultural_gender null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_family_consumer_science null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_health null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_history null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_humanities null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_language null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_legal null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_library null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_mathematics null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_mechanic_repair_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_military null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_multidiscipline null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_parks_recreation_fitness null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_personal_culinary null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_philosophy_religious null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_physical_science null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_precision_production null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_psychology null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_public_administration_social_service null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_resources null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_science_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_security_law_enforcement null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_social_science null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_theology_religious_vocation null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 academics__program_assoc_transportation null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.1044964

In [0]:
# GROUP BY FIELD
# 0 = Program not offered
# 1 = Program offered
# 2 = Program offered through an exclusively distance-education program
summary = df_union.groupBy(F.col('Field'), F.col('Value'))\
                  .agg( F.min('Income').alias('Min')\
                       ,F.expr('percentile_approx(Income, 0.25)').alias('25th')\
                       ,F.expr('percentile_approx(Income, 0.50)').alias('Median')\
                       ,F.expr('percentile_approx(Income, 0.75)').alias('75th')\
                       ,F.max('Income').alias('Max')\
                       ,F.avg('Income').alias('Mean')\
                       ,F.stddev('Income').alias('Std')\
                      )\
                  .orderBy(['Value', 'Field'])
display(summary)

Field Value Min 25th Median 75th Max Mean Std agriculture null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 architecture null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 biological null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 business_marketing null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 communication null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 communications_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 computer null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 construction null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 education null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 engineering null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 engineering_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 english null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 ethnic_cultural_gender null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 family_consumer_science null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 health null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 history null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 humanities null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 language null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 legal null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 library null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 mathematics null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 mechanic_repair_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 military null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 multidiscipline null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 parks_recreation_fitness null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 personal_culinary null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 philosophy_religious null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 physical_science null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 precision_production null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 psychology null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 public_administration_social_service null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 resources null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 science_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 security_law_enforcement null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 social_science null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 theology_religious_vocation null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 transportation null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 visual_performing null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 agriculture 0.0 9.4 22.8 28.6 35.5 151.5 30.501485318200842 11.414744749324896 architecture 0.0 9.4 22.9 28.5 35.3 151.5 30.38686995093422 11.242125680607113 biological 0.0 9.4 22.4 27.9 34.6 151.5 29.998619195884643 11.39023213404791 business_marketing 0.0 9.4 21.9 28.0 35.6 151.5 30.348914366013734 12.277485277431309 communication 0.0 9.4 22.6 28.1 34.9 151.5 30.15945327017193 11.372770880691856 communications_technology 0.0 9.4 22.8 28.5 35.6 151.5 30.480697505449246 11.435442149754808 computer 0.0 9.4 22.2 28.1 35.4 151.5 30.24982813760945 11.829167748232473 construction 0.0 9.4 22.8 28.8 35.8 151.5 30.69731961750216 11.569524362560102 education 0.0 9.4 22.4 28.1 35.2 151.5 30.253272768310563 11.650153542772971 engineering 0.0 9.4 22.6 28.3 35.1 151.5 30.250022016162436 11.3197663124

In [0]:
# GROUP BY DISCIPLINE
# 0 = Program not offered
# 1 = Program offered
# 2 = Program offered through an exclusively distance-education program
summary = df_union.groupBy(F.col('Discipline'), F.col('Value'))\
                  .agg( F.min('Income').alias('Min')\
                       ,F.expr('percentile_approx(Income, 0.25)').alias('25th')\
                       ,F.expr('percentile_approx(Income, 0.50)').alias('Median')\
                       ,F.expr('percentile_approx(Income, 0.75)').alias('75th')\
                       ,F.max('Income').alias('Max')\
                       ,F.avg('Income').alias('Mean')\
                       ,F.stddev('Income').alias('Std')\
                      )\
                  .orderBy(['Value', 'Discipline'])
display(summary)

Discipline Value Min 25th Median 75th Max Mean Std Arts null 13.4 23.9 30.9 42.8 73.0 33.357142857142904 12.096170938864269 Bus_Edu null 13.4 23.9 30.9 42.8 73.0 33.357142857142826 12.096355763252614 Health null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.096864074008169 Other null 13.4 23.9 30.9 42.8 73.0 33.35714285714284 12.096228695575563 STEM null 13.4 23.9 30.9 42.8 73.0 33.357142857142925 12.096158104151892 Arts 0.0 9.4 22.6 28.2 35.0 151.5 30.213292392479147 11.424678980503337 Bus_Edu 0.0 9.4 22.4 28.1 35.2 151.5 30.227385535307498 11.645732279996583 Health 0.0 9.4 22.3 28.1 35.1 151.5 30.190198235361503 11.698917044131395 Other 0.0 9.4 22.7 28.7 35.8 151.5 30.663956401883013 11.639013752127802 STEM 0.0 9.4 22.6 28.3 35.1 151.5 30.275153867696574 11.380070720008186 Arts 1.0 11.9 27.9 32.2 37.7 105.8 33.586974315764124 8.388241014997547 Bus_Edu 1.0 11.6 26.5 30.6 36.1 109.5 31.941357059764435 8.422002998924592 Health 1.0 11.3 25.7 30.0 36.0 111.0 31.562014680316782 9.255510300139134 Other 1.0 9.4 24.7 28.1 32.1 90.6 28.718504056229385 6.674907417658359 STEM 1.0 12.1 27.7 31.9 37.4 111.0 33.37567648927987 8.685123177364312 Arts 2.0 15.8 27.6 31.5 37.5 72.7 32.76753323485967 7.1077635006130775 Bus_Edu 2.0 15.8 26.6 30.6 36.3 72.7 31.82779163203104 7.412972959513453 Health 2.0 15.8 26.5 30.7 36.7 84.2 31.98003056546103 7.895922030298006 Other 2.0 11.1 25.3 28.5 32.1 61.4 29.496059394631654 6.248742018377634 STEM 2.0 15.8 28.2 32.0 38.4 72.7 33.344251968503926 7.112218324777922

In [0]:
# GROUP BY DEGREE
# 0 = Program not offered
# 1 = Program offered
# 2 = Program offered through an exclusively distance-education program
summary = df_union.groupBy(F.col('Degree'), F.col('Value'))\
                  .agg( F.min('Income').alias('Min')\
                       ,F.expr('percentile_approx(Income, 0.25)').alias('25th')\
                       ,F.expr('percentile_approx(Income, 0.50)').alias('Median')\
                       ,F.expr('percentile_approx(Income, 0.75)').alias('75th')\
                       ,F.max('Income').alias('Max')\
                       ,F.avg('Income').alias('Mean')\
                       ,F.stddev('Income').alias('Std')\
                      )\
                  .orderBy(['Value', 'Degree'])
display(summary)

Degree Value Min 25th Median 75th Max Mean Std assoc null 13.4 23.9 30.9 42.8 73.0 33.35714285714283 12.096239841702799 bachelors null 13.4 23.9 30.9 42.8 73.0 33.35714285714283 12.096239841702799 certificate null 13.4 23.9 30.9 42.8 73.0 33.357142857142975 12.096091229206325 assoc 0.0 9.4 22.4 28.3 35.6 151.5 30.44357950507203 11.756945044066875 bachelors 0.0 9.4 22.2 27.3 33.5 151.5 29.37441975438109 11.195044854743413 certificate 0.0 9.4 22.8 28.6 35.6 151.5 30.58368599269715 11.491498212032635 assoc 1.0 13.3 26.3 29.6 33.8 102.5 30.70771115443385 7.04227286734315 bachelors 1.0 11.9 31.7 36.0 41.1 111.0 37.132756853396884 9.245946089637227 certificate 1.0 9.4 25.0 28.1 31.7 109.5 28.811333506854062 6.626503198767937 assoc 2.0 15.8 25.9 29.0 32.1 64.9 29.951869246665407 6.235184151403687 bachelors 2.0 15.8 31.2 35.4 39.8 84.2 35.83310166799046 6.989848674964069 certificate 2.0 11.1 25.1 28.2 32.1 73.1 29.452952586206887 6.663853642246923

In [0]:
# GROUP BY FIELD & DEGREE
# 0 = Program not offered
# 1 = Program offered
# 2 = Program offered through an exclusively distance-education program
summary = df_union.groupBy(F.col('Degree'), F.col('Field'), F.col('Value'))\
                  .agg( F.min('Income').alias('Min')\
                       ,F.expr('percentile_approx(Income, 0.25)').alias('25th')\
                       ,F.expr('percentile_approx(Income, 0.50)').alias('Median')\
                       ,F.expr('percentile_approx(Income, 0.75)').alias('75th')\
                       ,F.max('Income').alias('Max')\
                       ,F.avg('Income').alias('Mean')\
                       ,F.stddev('Income').alias('Std')\
                      )\
                  .orderBy(['Value', 'Degree', 'Field'])
display(summary)

Degree Field Value Min 25th Median 75th Max Mean Std assoc agriculture null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc architecture null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc biological null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc business_marketing null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc communication null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc communications_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc computer null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc construction null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc education null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc engineering null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc engineering_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc english null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc ethnic_cultural_gender null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc family_consumer_science null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc health null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc history null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc humanities null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc language null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc legal null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc library null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc mathematics null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc mechanic_repair_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc military null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc multidiscipline null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc parks_recreation_fitness null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc personal_culinary null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc philosophy_religious null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc physical_science null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc precision_production null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc psychology null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc public_administration_social_service null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc resources null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc science_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc security_law_enforcement null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc social_science null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc theology_religious_vocation null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc transportation null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 assoc visual_performing null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 bachelors agriculture null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 bachelors architecture null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 bachelors biological null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 bachelors business_marketing null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 bachelors communication null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 bachelors communications_technology null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.10449643318638 bachelors computer null 13.4 23.9 30.9 42.8 73.0 3

In [0]:
# GROUP BY DISCIPLINE & DEGREE
# 0 = Program not offered
# 1 = Program offered
# 2 = Program offered through an exclusively distance-education program
summary = df_union.groupBy(F.col('Degree'), F.col('Discipline'), F.col('Value'))\
                  .agg( F.min('Income').alias('Min')\
                       ,F.expr('percentile_approx(Income, 0.25)').alias('25th')\
                       ,F.expr('percentile_approx(Income, 0.50)').alias('Median')\
                       ,F.expr('percentile_approx(Income, 0.75)').alias('75th')\
                       ,F.max('Income').alias('Max')\
                       ,F.avg('Income').alias('Mean')\
                       ,F.stddev('Income').alias('Std')\
                      )\
                  .orderBy(['Value', 'Degree', 'Discipline'])
display(summary)

Degree Discipline Value Min 25th Median 75th Max Mean Std assoc Arts null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.096787053107972 assoc Bus_Edu null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 assoc Health null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.100254450777097 assoc Other null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.09707588906976 assoc STEM null 13.4 23.9 30.9 42.8 73.0 33.357142857142854 12.096722870148284 bachelors Arts null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.096787053107972 bachelors Bus_Edu null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097711401020314 bachelors Health null 13.4 23.9 30.9 42.8 73.0 33.35714285714286 12.100254450777097 bachelors Other null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.09707588906976 bachelors STEM null 13.4 23.9 30.9 42.8 73.0 33.357142857142854 12.096722870148284 certificate Arts null 13.4 23.9 30.9 42.8 73.0 33.35714285714283 12.096273618034093 certificate Bus_Edu null 13.4 23.9 30.9 42.8 73.0 33.35714285714284 12.096581671233002 certificate Health null 13.4 23.9 30.9 42.8 73.0 33.35714285714287 12.097428938899517 certificate Other null 13.4 23.9 30.9 42.8 73.0 33.357142857142826 12.096369882130587 certificate STEM null 13.4 23.9 30.9 42.8 73.0 33.35714285714283 12.096252226324752 assoc Arts 0.0 9.4 22.4 28.2 35.4 151.5 30.34135805516133 11.61616836986644 assoc Bus_Edu 0.0 9.4 22.1 28.1 35.8 151.5 30.441956428087863 12.0943649390545 assoc Health 0.0 9.4 21.9 28.0 35.6 151.5 30.319021716389795 12.192962936215936 assoc Other 0.0 9.4 22.3 28.6 36.1 151.5 30.686775906457818 11.930902038858017 assoc STEM 0.0 9.4 22.5 28.3 35.5 151.5 30.401337873044618 11.58720107476706 bachelors Arts 0.0 9.4 22.0 27.2 33.2 151.5 29.189135334122 11.211730853816574 bachelors Bus_Edu 0.0 9.4 21.8 26.7 32.5 151.5 28.688548516187737 11.147170611718977 bachelors Health 0.0 9.4 21.4 26.2 31.3 151.5 27.918415882967597 10.624145757651988 bachelors Other 0.0 9.4 22.6 28.1 34.8 151.5 30.143911655961002 11.376745624865398 bachelors STEM 0.0 9.4 22.3 27.5 33.6 151.5 29.44568639725487 11.103621715006156 certificate Arts 0.0 9.4 22.8 28.5 35.5 151.5 30.47218244108702 11.4093409263076 certificate Bus_Edu 0.0 9.4 22.6 28.6 35.7 151.5 30.60543681989185 11.616062021177806 certificate Health 0.0 9.4 22.7 28.9 36.0 151.5 30.807350657791787 11.769009976320888 certificate Other 0.0 9.4 22.9 28.9 36.0 151.5 30.8362049057985 11.630120239253179 certificate STEM 0.0 9.4 22.8 28.5 35.5 151.5 30.4866687373652 11.385824877460358 assoc Arts 1.0 13.3 27.0 30.4 35.1 102.5 31.68130688448075 7.1788585254105515 assoc Bus_Edu 1.0 13.3 26.1 29.6 34.0 102.5 30.6454574272491 7.201513982554264 assoc Health 1.0 13.3 25.8 29.6 34.9 102.5 30.9446090335114 8.279998728775453 assoc Other 1.0 13.5 25.6 28.5 32.3 76.7 29.272793663277334 5.8049073291053865 assoc STEM 1.0 13.3 26.7 30.0 34.3 102.5 31.172545090180343 7.045750251807554 bachelors Arts 1.0 11.9 32.0 36.1 41.1 105.8 37.219229239723816 8.914399990245844 bachelors Bus_Edu 1.0 15.3 31.3 35.7 41.0 105.8 36.776367924528316 9.345392823115954 bachelors Health 1.0 15.3 31.7 36.1 41.5 111.0 37.46298566000737 10.085122518271481 bachelors Other 1.0 15.3 30.5 34.4 38.9 90.6 35.182692790756086 8.016166110679189 bachelors STEM 1.0 15.3 32.3 36.5 41.8 111.0 37.84458502461352 9.537747391037843 certificate Arts 1.0 12.1 26.3 29.1 32.9 82.9 30.456380424746094 6.642000250763803 certificate Bus_Edu 1.0 11.6 25.2 28.2 32.0 109.5 29.178642911636697 6.732860690382613 certificate Health 1.0 11.3 23.9 27.5 31.7 106.0 28.626099406831653 7.625609673520268 certificate Other 1.0 9.4 23.6 27.0 30.2 70.5 27.05991076257436 5.800443752380782 certificate STEM 1.0 12.1 26.1 28.9 32.5 70.5 30.014585663446844 6.355463994664799 assoc Arts 2.0 15.8 26.3 29.4 33.6 61.4 30.802246181491466 6.437170357876091 assoc Bus_Edu 2.0 15.8 25.8 28.9 32.1 61.4 29.78745819397994 6.429971132434513 assoc Health 2.0 15.8 25.8 29.0 32.7 64.9 30.087096774193544 6.822915191628782 assoc Other 2.0 15.8

In [0]:
# Count # of fields and degrees offered
df_drop1 = df_drop.withColumn('#degrees'    , sum([F.when(F.col(c).cast(IntegerType())==1,1).otherwise(0).alias(c) for c in degrees]))\
                  .withColumn('#assoc'      , sum([F.when(F.col(c).cast(IntegerType())==1,1).otherwise(0).alias(c) for c in academics__program_assoc]))\
                  .withColumn('#bachelors'  , sum([F.when(F.col(c).cast(IntegerType())> 1,1).otherwise(0).alias(c) for c in academics__program_bachelors]))\
                  .withColumn('#certificate', sum([F.when(F.col(c).cast(IntegerType())==1,1).otherwise(0).alias(c) for c in sum([academics__program_certificate_lt_1,\
                                                                                                                                 academics__program_certificate_lt_2,\
                                                                                                                                 academics__program_certificate_lt_4],[])]))
                  #.withColumn('#certificate1', sum([F.when(F.col(c).cast(IntegerType())=1,1).otherwise(0).alias(c) for c in academics__program_certificate_lt_1]))\
                  #.withColumn('#certificate2', sum([F.when(F.col(c).cast(IntegerType())=1,1).otherwise(0).alias(c) for c in academics__program_certificate_lt_2]))\
                  #.withColumn('#certificate4', sum([F.when(F.col(c).cast(IntegerType())=1,1).otherwise(0).alias(c) for c in academics__program_certificate_lt_4]))\

df_drop2 = df_drop1.withColumn('HighEarning', F.when((F.col('#assoc')       > 0) | \
                                                     (F.col('#bachelors')   > 0) | \
                                                     (F.col('#certificate') > 0), 1)\
                                               .otherwise(0))
display(df_drop2)

row_id academics__program_assoc_agriculture academics__program_assoc_architecture academics__program_assoc_biological academics__program_assoc_business_marketing academics__program_assoc_communication academics__program_assoc_communications_technology academics__program_assoc_computer academics__program_assoc_construction academics__program_assoc_education academics__program_assoc_engineering academics__program_assoc_engineering_technology academics__program_assoc_english academics__program_assoc_ethnic_cultural_gender academics__program_assoc_family_consumer_science academics__program_assoc_health academics__program_assoc_history academics__program_assoc_humanities academics__program_assoc_language academics__program_assoc_legal academics__program_assoc_library academics__program_assoc_mathematics academics__program_assoc_mechanic_repair_technology academics__program_assoc_military academics__program_assoc_multidiscipline academics__program_assoc_parks_recreation_fitness academics__program_assoc_personal_culinary academics__program_assoc_philosophy_religious academics__program_assoc_physical_science academics__program_assoc_precision_production academics__program_assoc_psychology academics__program_assoc_public_administration_social_service academics__program_assoc_resources academics__program_assoc_science_technology academics__program_assoc_security_law_enforcement academics__program_assoc_social_science academics__program_assoc_theology_religious_vocation academics__program_assoc_transportation academics__program_assoc_visual_performing academics__program_bachelors_agriculture academics__program_bachelors_architecture academics__program_bachelors_biological academics__program_bachelors_business_marketing academics__program_bachelors_communication academics__program_bachelors_communications_technology academics__program_bachelors_computer academics__program_bachelors_construction academics__program_bachelors_education academics__program_bachelors_engineering academics__program_bachelors_engineering_technology academics__program_bachelors_english academics__program_bachelors_ethnic_cultural_gender academics__program_bachelors_family_consumer_science academics__program_bachelors_health academics__program_bachelors_history academics__program_bachelors_humanities academics__program_bachelors_language academics__program_bachelors_legal academics__program_bachelors_library academics__program_bachelors_mathematics academics__program_bachelors_mechanic_repair_technology academics__program_bachelors_military academics__program_bachelors_multidiscipline academics__program_bachelors_parks_recreation_fitness academics__program_bachelors_personal_culinary academics__program_bachelors_philosophy_religious academics__program_bachelors_physical_science academics__program_bachelors_precision_production academics__program_bachelors_psychology academics__program_bachelors_public_administration_social_service academics__program_bachelors_resources academics__program_bachelors_science_technology academics__program_bachelors_security_law_enforcement academics__program_bachelors_social_science academics__program_bachelors_theology_religious_vocation academics__program_bachelors_transportation academics__program_bachelors_visual_performing academics__program_certificate_lt_1_yr_agriculture academics__program_certificate_lt_1_yr_architecture academics__program_certificate_lt_1_yr_biological academics__program_certificate_lt_1_yr_business_marketing academics__program_certificate_lt_1_yr_communication academics__program_certificate_lt_1_yr_communications_technology academics__program_certificate_lt_1_yr_computer academics__program_certificate_lt_1_yr_construction academics__program_certificate_lt_1_yr_education academics__program_certificate_lt_1_yr_engineering academics__program_certificate_lt_1_yr_engineering_technology academics__program_certificate_lt_1_yr_english academics__program_certificate_lt_1_yr_ethnic_cultural_gender academics__program_ce

In [0]:
# Get 75th percentile for each ACADEMICS. Mark if above median and offered by institution.
byDegree = df_union.groupBy(F.col('Degree'), F.col('Value'))\
                   .agg( F.min('Income').alias('Min')\
                        ,F.expr('percentile_approx(Income, 0.25)').alias('25th')\
                        ,F.expr('percentile_approx(Income, 0.50)').alias('Median')\
                        ,F.expr('percentile_approx(Income, 0.75)').alias('75th')\
                        ,F.max('Income').alias('Max')\
                        ,F.avg('Income').alias('Mean')\
                        ,F.stddev('Income').alias('Std')\
                       )\
                   .orderBy(['Value', 'Degree'])
display(byDegree)

In [0]:
display(df_drop2.groupBy(F.col('HighEarning'))\
                .agg( F.min('Income').alias('Min')\
                                ,F.expr('percentile_approx(Income, 0.25)').alias('25th')\
                                ,F.expr('percentile_approx(Income, 0.50)').alias('Median')\
                                ,F.expr('percentile_approx(Income, 0.75)').alias('75th')\
                                ,F.max('Income').alias('Max')\
                                ,F.avg('Income').alias('Mean')\
                                ,F.stddev('Income').alias('Std')\
                               )
       )

HighEarning Min 25th Median 75th Max Mean Std 1 9.4 22.1 27.2 33.0 109.5 28.486694933840173 9.188070226354634 0 11.9 32.1 37.2 44.6 151.5 40.475644804716296 14.807850003232826

####2.2) Discretize

In [0]:
_categorical = [i[0] for i in df_drop2.dtypes if i[1] == 'string']


In [0]:
from pyspark.ml.feature import OneHotEncoder

df = spark.createDataFrame([
    (0.0, 1.0),
    (1.0, 0.0),
    (2.0, 1.0),
    (0.0, 2.0),
    (0.0, 1.0),
    (2.0, 0.0)
], ["categoryIndex1", "categoryIndex2"])

encoder = OneHotEncoder(inputCols=["categoryIndex1", "categoryIndex2"],
                        outputCols=["categoryVec1", "categoryVec2"])
model = encoder.fit(df)
encoded = model.transform(df)
encoded.show()

+--------------+--------------+-------------+-------------+
categoryIndex1|categoryIndex2| categoryVec1| categoryVec2|
+--------------+--------------+-------------+-------------+
 0.0| 1.0|(2,[0],[1.0])|(2,[1],[1.0])|
 1.0| 0.0|(2,[1],[1.0])|(2,[0],[1.0])|
 2.0| 1.0| (2,[],[])|(2,[1],[1.0])|
 0.0| 2.0|(2,[0],[1.0])| (2,[],[])|
 0.0| 1.0|(2,[0],[1.0])|(2,[1],[1.0])|
 2.0| 0.0| (2,[],[])|(2,[0],[1.0])|
+--------------+--------------+-------------+-------------+